### W231: Eviction Notices

In [1]:
from __future__ import division
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import folium
from folium.plugins import MarkerCluster
%matplotlib inline

In [12]:
evictions = pd.read_csv('Eviction_Notices.csv', index_col=0)

In [10]:
evictions.head()

Address           City State    Zip  \
Eviction_ID                                                              
M153486         0 Block of Raymond  Avenue  San Francisco    CA  94134   
M153490       2700 Block of Folsom  Street  San Francisco    CA  94110   
M153487       300 Block of San Benito  Way  San Francisco    CA  94127   
M153438        100 Block of Elmira  Street  San Francisco    CA  94124   
M153488      0 Block of Morningside  Drive  San Francisco    CA  94132   

              File Date Non Payment Breach Nuisance Illegal Use  \
Eviction_ID                                                       
M153486      12/30/2015       False  False    False       False   
M153490      12/30/2015       False   True    False       False   
M153487      12/30/2015       False  False     True       False   
M153438      12/30/2015       False  False    False       False   
M153488      12/30/2015        True  False    False       False   

            Failure to Sign Renewal                  ...                    \
Eviction_ID                                          ...                     
M153486                       False                  ...                     
M153490                       False                  ...                     
M153487                       False                  ...                     
M153438                       False                  ...                     
M153488                       False                  ...                     

            Other Cause Late Payments Lead Remediation Development  \
Eviction_ID                                                          
M153486           False         False            False       False   
M153490           False         False            False       False   
M153487           False         False            False       False   
M153438           False         False            False       False   
M153488           False         False            False       False   

            Good Samaritan Ends Constraints Constraints Date  \
Eviction_ID                                                    
M153486                     NaN       False              NaN   
M153490                     NaN       False              NaN   
M153487                     NaN       False              NaN   
M153438                     NaN       False       02/26/2021   
M153488                     NaN       False              NaN   

            Supervisor_District           Neighborhood  \
Eviction_ID                                              
M153486                      10      Visitacion Valley   
M153490                       9                Mission   
M153487                       7     West of Twin Peaks   
M153438                      10  Bayview Hunters Point   
M153488                       7        Sunset/Parkside   

                                   Client_Location  
Eviction_ID                                         
M153486      (37.7121484523486, -122.404287840075)  
M153490       (37.7532984475532, -122.41422876374)  
M153487      (37.7296676394739, -122.467418596281)  
M153438       (37.7353069212531, -122.40373356189)  
M153488      (37.7331813515864, -122.492299907103)  

[5 rows x 29 columns]

### Filter to dates after 2010

In [13]:
evictions['File Date'] = pd.to_datetime(evictions['File Date'], dayfirst=True)

In [14]:
evictions = evictions[evictions['File Date'].dt.year >= 2010]

### Extract latitude, longitude

In [15]:
evictions = evictions.replace('1 QNAN\n', np.nan)

In [16]:
evictions['latitude'] = evictions['Client_Location'].str.strip('()').str.split(', ').str.get(0).astype(float)
evictions['longitude'] = evictions['Client_Location'].str.strip('()').str.split(', ').str.get(1).astype(float)

### Filter nulls

In [17]:
# Filter out null location values
evictions = evictions[evictions['longitude'].notnull()]

### Evictions with Late Payments

In [18]:
problem_evictions = evictions[evictions['Non Payment'] | evictions['Breach'] | 
          evictions['Breach'] | evictions['Nuisance'] | 
          evictions['Illegal Use']]

In [22]:
len(problem_evictions)

5925

In [21]:
# Export
problem_evictions.to_csv('problem_evictions.csv')

### Map

In [23]:
def show_map(df):
    SF_COORDINATES = (37.78, -122.45)
    # Create map
    tiles = r'https://api.mapbox.com/v4/mapbox.streets/{z}/{x}/{y}.png?access_token=pk.eyJ1Ijoia29ubmlhbWNoYW4iLCJhIjoiY2loZjZ1aDB4MGxxaHR0bHpmMDRrczNubCJ9.42XTV2wAGebwq8n5KvJBxQ'
    attr = '© Mapbox, © OpenStreetMap'
    eviction_map = folium.Map(location=SF_COORDINATES, tiles=tiles, zoom_start=13, attr=attr)
    
    # Cluster
#     notices = zip(df['latitude'], df['longitude'])
#     eviction_map.add_children(MarkerCluster(locations=notices,
#                                             popups=df.index))
    # Individual markers
    for index, row in df.iterrows():
        folium.CircleMarker(location=(row['latitude'], row['longitude']), radius=1, popup=index).add_to(eviction_map)        
    return eviction_map

show_map(problem_evictions)